In [9]:
import openreview
import pandas as pd
import datetime as date
import tqdm
import nltk; nltk.download('punkt')
import convokit
from convokit import Corpus, download
from convokit import TextParser
from convokit import PolitenessStrategies

import random
from sklearn import svm
from scipy.sparse import csr_matrix
from sklearn.metrics import classification_report
from convokit import Classifier

[nltk_data] Downloading package punkt to
[nltk_data]     /Users/raymondeds/nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [14]:
df_convokit = pd.read_csv('./data/submissions/df_convokit.csv')
df_convokit.columns=['id','timestamp','speaker','reply_to','conversation_id','year','text']
new_corpus = Corpus.from_pandas(df_convokit)

In [24]:
#This is my corpus
parser = TextParser(verbosity=1000)
new_corpus = parser.transform(new_corpus)
ps = PolitenessStrategies()
new_corpus = ps.transform(new_corpus, markers=True)

1000/22878 utterances processed
2000/22878 utterances processed
3000/22878 utterances processed
4000/22878 utterances processed
5000/22878 utterances processed
6000/22878 utterances processed
7000/22878 utterances processed
8000/22878 utterances processed
9000/22878 utterances processed
10000/22878 utterances processed
11000/22878 utterances processed
12000/22878 utterances processed
13000/22878 utterances processed
14000/22878 utterances processed
15000/22878 utterances processed
16000/22878 utterances processed
17000/22878 utterances processed
18000/22878 utterances processed
19000/22878 utterances processed
20000/22878 utterances processed
21000/22878 utterances processed
22000/22878 utterances processed
22878/22878 utterances processed


In [25]:
new_corpus.dump(name='corpus_rr',base_path='./data/')

In [30]:
data = ps.summarize(new_corpus, plot=True)

In [35]:
stack_exchange_corpus = "stack-exchange-politeness-corpus"

wiki_corpus = Corpus(download("wikipedia-politeness-corpus"))
wiki_corpus = parser.transform(wiki_corpus)
wiki_corpus = ps.transform(wiki_corpus, markers=True)
binary_corpus = Corpus(utterances=[utt for utt in wiki_corpus.iter_utterances() if utt.meta["Binary"] != 0])

clf = Classifier(obj_type="utterance", 
                        pred_feats=["politeness_strategies"], 
                        labeller=lambda utt: utt.meta['Binary'] == 1)
clf.fit(binary_corpus)


Dataset already exists at /Users/raymondeds/.convokit/downloads/wikipedia-politeness-corpus
1000/4353 utterances processed
2000/4353 utterances processed
3000/4353 utterances processed
4000/4353 utterances processed
4353/4353 utterances processed
Initialized default classification model (standard scaled logistic regression).


In [36]:
out = clf.transform(new_corpus)


prediction  pred_score
id                                
rkKe7upMe            0    0.012231
ByEeLZ5xz            0    0.013961
BkB8c0fEe            0    0.013961
B1LfYs_gf            0    0.013961
B1xMP0uF3X           0    0.014170
...                ...         ...
Hkl-Ujd9eN           1    0.999952
BJVf3P67G            1    0.999975
rkg0svOopQ           1    0.999982
HJHZf2b4e            1    0.999987
rkxDV6Bt6m           1    0.999992

[22878 rows x 2 columns]

In [38]:
pred2label = {1: "polite", 0: "impolite"}

for i, idx in enumerate(new_corpus.get_utterance_ids()):
    print(i)
    test_utt = new_corpus.get_utterance(idx)
    ypred, yprob = test_utt.meta['prediction'], test_utt.meta['pred_score']
    print("R&R Text:\n{}".format(test_utt.text))
    print("------------------------")
    print("Result: {}, probability estimates = {}\n".format(pred2label[ypred], yprob))

0
R&R Text:
I thank the authors for their response and explanations. My primary objections to this paper are not based on performance, but (in my view) lack of sufficiently clear and careful testing of ideas.

I partly agree with the authors regarding comparison to Inception networks specifially due to the join operation used by FractalNet which Inception does not use. Clearly, there are differences, and my use of the word 'direct' was incorrect. Nevertheless, I think the (indirect) relations are important because they may point the authors towards helpful baselines. More on this later.

I also agree that the any time property enabled by FractalNet+drop-path appears to be stonger than what's been shown for Resnets/Highways. However, firstly, this does not mean that they do not have this property at all.

(Due to the above two points, I am raising my score by one point)

The second point relates to my earlier concern about clear and careful comparisons and testing, which the authors hav

Result: polite, probability estimates = 0.5809379158648034

639
R&R Text:
I also found the way this was presented to be quite hard to understand. I think that now I get it.
------------------------
Result: impolite, probability estimates = 0.484029379488617

640
R&R Text:
The paper presents a method for joint motion prediction and activity classification from sequences with two different applications: motion of fruit flies and online handwriting recognition.

The method uses a classical encoder-decoder pipeline, with skip connections allowing direct communication between the encoder and the decoder on respective levels of abstraction.
Motion is discretized and predicted using classification. The model is trained on classification loss combined with a loss on motion prediction. The goal is to leverage latter loss in a semi-supervised setting from parts of the data which do not contain action labels.

The idea of leveraging predictions to train feature representations for discrimination 

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




R&R Text:
Thanks again, AC. We've updated the title of the comment and added a note at the top.
------------------------
Result: polite, probability estimates = 0.9746664111556739

9638
R&R Text:
I understand that this was in response to an earlier public comment. It would have been better to respond directly to that comment to avoid confusion. While the timestamp should make clear that this is not a response to reviewers, there is still scope for confusion. I recommend editing this comment to add, at the top, that it's a reply to the comment below.
------------------------
Result: impolite, probability estimates = 0.4431001604371391

9639
R&R Text:
Thank you, AC. We agree and will follow your suggestion. The response here was posted a while ago, and is actually not to the official reviews, but to the earlier public comment. We're still working on the response to official reviews and will post them separately once they are ready.
------------------------
Result: polite, probability es

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




------------------------
Result: impolite, probability estimates = 0.26531912941640856

20011
R&R Text:
This paper proposes a neural model for synthesizing instrument sounds, using an architecture based on the WaveNet and DeepVoice models. The model generates raw waveforms conditioned on a piano roll representation of aligned MIDI input.

My biggest gripe with this work is that the model is trained entirely on a synthetic dataset generated from a sample-based synthesizer using a sound font. I feel that this defeats the purpose, as it will never work better than just sampling the original sound library. One potential argument in favour would be to save storage space, but the sound font used for the work is only ~140 MB, which is not prohibitive these days (indeed, many neural models require a comparable amount of storage).

It would be much more interesting to train the model on real instrument recordings, because then it could capture all the nuances of the instruments that sample-bas

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [45]:
df_rr_predict_score = pd.DataFrame(clf.summarize(out))
df_rr_predict_score['id'] = df_rr_predict_score.index
df_rr_predict_score.to_csv('./data/submissions/df_rr_politeness_score.csv',index=False)